## Imports 

In [2]:
import argparse
import easydict
import numpy as np
import pandas as pd
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.models import load_model
from matplotlib import pyplot as plt
from plotread import *
import shap
import pickle
import ipywidgets as widgets
from collections import Counter
%matplotlib inline

import warnings
warnings.filterwarnings("ignore")

# init the JS visualization code
shap.initjs()

In [3]:
import tensorflow._api.v2.compat.v1 as tf
from tensorflow.compat.v1.keras.backend import get_session
tf.compat.v1.disable_v2_behavior()
tf.compat.v1.disable_eager_execution()
from tensorflow.python.ops.numpy_ops import np_config
np_config.enable_numpy_behavior()

Instructions for updating:
non-resource variables are not supported in the long term


## Functions 

In [4]:
def main():
    ###########################################################################
    # Parser Definition
    ###########################################################################
    opt = easydict.EasyDict({
        "model": "GRU",
        "datapath": "Dataset1/",
        "savepath": "Experiment1/GRU/8/Garbage/Run50/",
        "extension": ".dat",
        "batch_size": 32,
        "plots_in": False,
        "plots_out": True
    })

    ###########################################################################
    # Variables Definition
    ###########################################################################
    nin = ['time', 'PLML2', 'PLMR', 'AVBL', 'AVBR']
    nout = ['time', 'DB1', 'LUAL', 'PVR', 'VB1']
    neurons = ['time','DB1','LUAL','PVR','VB1','PLML2','PLMR','AVBL','AVBR']

    ###########################################################################
    # Read data
    ###########################################################################
    files = getdata(opt.datapath, opt.extension)
    train, valid, test = splitdata(files)
    trainx, trainy = readdata(opt.datapath, train, neurons, nin, nout)
    validx, validy = readdata(opt.datapath, valid, neurons, nin, nout)
    testx, testy = readdata(opt.datapath, test, neurons, nin, nout)
    if opt.plots_in:
        plotdata(trainx, '/train_data', '/x', opt.model, opt.savepath)
        plotdata(trainy, '/train_data', '/y', opt.model, opt.savepath)
        plotdata(validx, '/valid_data', '/x', opt.model, opt.savepath)
        plotdata(validy, '/valid_data', '/y', opt.model, opt.savepath)
        plotdata(testx, '/test_data', '/x', opt.model, opt.savepath)
        plotdata(testy, '/test_data', '/y', opt.model, opt.savepath)
        
    ###########################################################################
    # Load Model and Evaluate
    ###########################################################################
    output_size = 4
    global model
    model = load_model(opt.savepath + 'model.h5')
    model.summary()

    print("Starting to explain...")
    X_train = np.array(trainx)
    X_test = np.array(testx)

    nin_names = nin[1:len(nin)]

    return X_train, X_test, nin_names

## Code 

In [5]:
X_train, X_test, nin_names = main()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 gru (GRU)                   (None, 50, 8)             336       
                                                                 
 time_distributed (TimeDistr  (None, 50, 4)            36        
 ibuted)                                                         
                                                                 
 flatten (Flatten)           (None, 200)               0         
                                                                 
Total params: 372
Trainable params: 372
Non-trainable params: 0
_________________________________________________________________
Starting to explain...


In [6]:
X_train.shape

(20, 50, 4)

In [7]:
X_test.shape

(10, 50, 4)

In [8]:
background = X_train[np.random.choice(X_train.shape[0], 1, replace=False)]
print("background.shape=")
print(background.shape)

background.shape=
(1, 50, 4)


In [9]:
background

array([[[0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0., 0., 0., 0.],
        [0.,

In [10]:
for layer in model.layers:
    print("LAYER")
    print(layer.name, layer.inbound_nodes, layer.outbound_nodes)
    print(layer.input_shape)
    print(layer.output_shape)

LAYER
gru [<keras.engine.node.Node object at 0x000001699949C790>] [<keras.engine.node.Node object at 0x00000169995EDEB0>]
(None, 50, 4)
(None, 50, 8)
LAYER
time_distributed [<keras.engine.node.Node object at 0x00000169995EDEB0>] [<keras.engine.node.Node object at 0x0000016999609DC0>]
(None, 50, 8)
(None, 50, 4)
LAYER
flatten [<keras.engine.node.Node object at 0x0000016999609DC0>] []
(None, 50, 4)
(None, 200)


In [11]:
X_test[:1,:,:]

array([[[1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1.4, 0. , 2.3, 0. ],
        [1

### explainers

In [12]:
# explainer1 = shap.DeepExplainer(model, X_train)
# explainer2 = shap.DeepExplainer(model, background)

explainer3 = shap.DeepExplainer((model.layers[0].input, model.layers[-1].output), X_train)
explainer4 = shap.DeepExplainer((model.layers[0].input, model.layers[-1].output), background)

# explainer5 = shap.GradientExplainer(model, X_train)
# explainer6 = shap.GradientExplainer(model, background)

# explainer7 = shap.GradientExplainer((model.layers[0].input, model.layers[-1].output), X_train)
# explainer8 = shap.GradientExplainer((model.layers[0].input, model.layers[-1].output), background)

### shap_values

#### Loading the shap_values from pickle files

In [13]:
list_of_shap_values = []

for i in range(1, 9):
    for j in range(1, 3):
        with open("D:\Pedro\IST\ANO 2\SEM 2\Tese\gmestre\ICLR-RNN-CElegans\Experiment1\GRU\8\Garbage\Run50\pickles\shap_values{}_explainer{}.pkl".format(j, i), 'rb') as file:
            shap_value = pickle.load(file)
            list_of_shap_values.append(shap_value)

In [14]:
# shap_values1_explainer1 = list_of_shap_values[0]
# shap_values2_explainer1 = list_of_shap_values[1]
# shap_values1_explainer2 = list_of_shap_values[2]
# shap_values2_explainer2 = list_of_shap_values[3]
shap_values1_explainer3 = list_of_shap_values[4]
shap_values2_explainer3 = list_of_shap_values[5]
shap_values1_explainer4 = list_of_shap_values[6]
shap_values2_explainer4 = list_of_shap_values[7]
# shap_values1_explainer5 = list_of_shap_values[8]
# shap_values2_explainer5 = list_of_shap_values[9]
# shap_values1_explainer6 = list_of_shap_values[10]
# shap_values2_explainer6 = list_of_shap_values[11]
# shap_values1_explainer7 = list_of_shap_values[12]
# shap_values2_explainer7 = list_of_shap_values[13]
# shap_values1_explainer8 = list_of_shap_values[14]
# shap_values2_explainer8 = list_of_shap_values[15]

#### Calculating shap_values
Below we have used explainer to generate shape values for the test dataset using the shap_values() method of explainer. The explainer object has a base value to which it adds shape values for a particular sample in order to generate a final prediction. The base value is stored in the expected_value attribute of the explainer object. All model predictions will be generated by adding shap values generated for a particular sample to this expected value.

In [ ]:
# shap_values1_explainer1 = explainer1.shap_values(X_test[:1,:,:])

In [ ]:
# shap_values2_explainer1 = explainer1.shap_values(X_test)

In [ ]:
# shap_values1_explainer2 = explainer2.shap_values(X_test[:1,:,:])

In [ ]:
# shap_values2_explainer2 = explainer2.shap_values(X_test)

In [ ]:
# shap_values1_explainer3 = explainer3.shap_values(X_test[:1,:,:])

In [ ]:
# shap_values2_explainer3 = explainer3.shap_values(X_test)

In [ ]:
# shap_values1_explainer4 = explainer4.shap_values(X_test[:1,:,:])

In [ ]:
# shap_values2_explainer4 = explainer4.shap_values(X_test)

In [ ]:
# shap_values1_explainer5 = explainer5.shap_values(X_test[:1,:,:])

In [ ]:
# shap_values2_explainer5 = explainer5.shap_values(X_test)

In [ ]:
# shap_values1_explainer6 = explainer6.shap_values(X_test[:1,:,:])

In [ ]:
# shap_values2_explainer6 = explainer6.shap_values(X_test)

In [ ]:
# shap_values1_explainer7 = explainer7.shap_values(X_test[:1,:,:])

In [ ]:
# shap_values2_explainer7 = explainer7.shap_values(X_test)

In [ ]:
# shap_values1_explainer8 = explainer8.shap_values(X_test[:1,:,:])

In [ ]:
# shap_values2_explainer8 = explainer8.shap_values(X_test)

#### Creating pickle files to save the shap_values

In [ ]:
# for i in range(1, 9):
#     for j in range(1, 3):
#         with open("D:\Pedro\IST\ANO 2\SEM 2\Tese\gmestre\ICLR-RNN-CElegans\Experiment1\GRU\8\Garbage\Run50\pickles\shap_values{}_explainer{}.pkl".format(j, i), 'wb') as file:
#             pickle.dump(eval("shap_values{}_explainer{}".format(j, i)), file)

#### Print shap_values

In [ ]:
# print(shap_values1_explainer1)
# print(shap_values2_explainer1)

In [ ]:
# print(shap_values1_explainer2)
# print(shap_values2_explainer2)

In [15]:
print(shap_values1_explainer3)
print(shap_values2_explainer3)

[array([[[ 0.00673788,  0.00340175,  0.03706466, -0.00788887],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
       

In [16]:
print(shap_values1_explainer4)
print(shap_values2_explainer4)

[array([[[-0.00192093,  0.        ,  0.04337845,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
        [ 0.        ,  0.        ,  0.        ,  0.        ],
       

In [ ]:
# print(shap_values1_explainer5)
# print(shap_values2_explainer5)

In [ ]:
# print(shap_values1_explainer6)
# print(shap_values2_explainer6)

In [ ]:
# print(shap_values1_explainer7)
# print(shap_values2_explainer7)

In [ ]:
# print(shap_values1_explainer8)
# print(shap_values2_explainer8)

In [17]:
# print(np.array(shap_values1_explainer1).shape)
# print(np.array(shap_values2_explainer1).shape)

# print(np.array(shap_values1_explainer2).shape)
# print(np.array(shap_values2_explainer2).shape)

print(np.array(shap_values1_explainer3).shape)
print(np.array(shap_values2_explainer3).shape)

print(np.array(shap_values1_explainer4).shape)
print(np.array(shap_values2_explainer4).shape)

# print(np.array(shap_values1_explainer5).shape)
# print(np.array(shap_values2_explainer5).shape)

# print(np.array(shap_values1_explainer6).shape)
# print(np.array(shap_values2_explainer6).shape)

# print(np.array(shap_values1_explainer7).shape)
# print(np.array(shap_values2_explainer7).shape)

# print(np.array(shap_values1_explainer8).shape)
# print(np.array(shap_values2_explainer8).shape)

(200, 1, 50, 4)
(200, 10, 50, 4)
(200, 1, 50, 4)
(200, 10, 50, 4)


In [18]:
shap_values1_explainer3_reshaped = np.reshape(np.array(shap_values1_explainer3), (200, 50, 4))

In [19]:
shap_values1_explainer3_reshaped.shape

(200, 50, 4)

In [20]:
shap_values1_explainer4_reshaped = np.reshape(np.array(shap_values1_explainer4), (200, 50, 4))

In [21]:
shap_values1_explainer4_reshaped.shape

(200, 50, 4)

### expected_values

In [22]:
# print(explainer1.expected_value)
# print(explainer2.expected_value)
print(explainer3.expected_value)
print(explainer4.expected_value)

[-0.02050989 -0.05383663 -0.05461215 -0.0328111  -0.04205898 -0.04598381
 -0.04370136 -0.0335195  -0.04860049 -0.04157876 -0.03602615 -0.03479258
 -0.04807583 -0.03812858 -0.03082505 -0.03491182 -0.04466021 -0.03505868
 -0.02746002 -0.03390639 -0.04041506 -0.03227394 -0.02534934 -0.0322119
 -0.03628609 -0.0297866  -0.02404123 -0.03023055 -0.03264996 -0.02761363
 -0.02322219 -0.02823454 -0.02960538 -0.02575265 -0.02268957 -0.0263772
 -0.02712541 -0.02418279 -0.02231889 -0.02472815 -0.02513481 -0.02287169
 -0.02203671 -0.02330531 -0.02354737 -0.02178254 -0.02180127 -0.02209841
 -0.02228258 -0.02087886 -0.0215898  -0.02108397 -0.02127154 -0.02012729
 -0.02139041 -0.02023419 -0.02045812 -0.01949882 -0.02119721 -0.01952169
 -0.01979773 -0.01896913 -0.02100759 -0.01892178 -0.01925567 -0.01851822
 -0.02082052 -0.01841316 -0.01880514 -0.01812992 -0.02063577 -0.01797815
 -0.01842552 -0.01779134 -0.02045344 -0.0176022  -0.01810107 -0.01749218
 -0.02027364 -0.01727359 -0.01745532 -0.01764749 -0.0

In [23]:
# print(explainer1.expected_value.shape)
# print(explainer2.expected_value.shape)
print(explainer3.expected_value.shape)
print(explainer4.expected_value.shape)

(200,)
(200,)


## Visualizations

### testing

In [ ]:
X_test[0][0]

In [ ]:
X_test[0][0].shape

In [ ]:
X_test[0][0].reshape(1,4).shape

In [ ]:
x_test_df = pd.DataFrame(data=X_test[0][0].reshape(1,4), columns = nin_names)

In [ ]:
x_test_df

In [ ]:
x_test_df.shape

In [ ]:
shap.force_plot(explainer2.expected_value[0], shap_values1_explainer2[0][0][0], x_test_df.iloc[0])

In [ ]:
x_test_df = pd.DataFrame(data = X_test[0,:,:], columns = nin_names)

In [ ]:
x_test_df

In [ ]:
shap_values1_explainer2[0][0].shape

In [ ]:
shap_values1_explainer2[0].shape

In [ ]:
len(explainer2.expected_value)

In [ ]:
# # IF USING THE WHOLE X_TEST
# for i in range(len(explainer2.expected_value)):
#     for j in range(np.array(shap_values1_explainer2).shape[1]):
#         x_test_df = pd.DataFrame(data=X_test, columns=nin_names)
#         force_plot = shap.force_plot(explainer2.expected_value[i], shap_values1_explainer2[i][j], x_test_df.iloc[i])

In [ ]:
for i in range(len(explainer2.expected_value)):
    for j in range(np.array(shap_values1_explainer2).shape[1]):
        x_test_df = pd.DataFrame(data=X_test[0], columns=nin_names)
        force_plot = shap.force_plot(explainer2.expected_value[i], shap_values1_explainer2[i][j], x_test_df)

In [ ]:
i = 0

x_test_df = pd.DataFrame(data = X_test[0], columns = nin_names)
shap.force_plot(explainer2.expected_value[0], shap_values1_explainer2[0][0], x_test_df)
## Problem:  Can not take into account many observations at the same time.
### The pic below explain for only 1 observation of 20 time steps, each time step has 10 features.

In [ ]:
################# Plot AVERAGE shap values for ALL observations  #####################
## Consider ABSOLUTE of SHAP values ##
shap_average_abs_value = np.abs(shap_values1_explainer2[0]).mean(axis=0)

x_average_value = pd.DataFrame(data = X_test.mean(axis=0), columns = nin_names)
shap.force_plot(0, shap_average_abs_value, x_average_value)

In [ ]:
i = 0
shap.force_plot(0, shap_average_abs_value[i], x_average_value.iloc[i,:])

In [ ]:
################# Plot AVERAGE shap values for ALL observations  #####################
## Consider average (+ is different from -)
shap_average_value = shap_values1_explainer2[0].mean(axis=0)

x_average_value = pd.DataFrame(data = X_test.mean(axis=0), columns = nin_names)
shap.force_plot(explainer2.expected_value[0], shap_average_value, x_average_value)

In [ ]:
i = 0
shap.force_plot(explainer2.expected_value[0], shap_average_value[i], x_average_value.iloc[i,:])

In [ ]:
shap_values_2D = shap_values1_explainer2[0].reshape(-1,4)
X_test_2D = X_test.reshape(-1,4)


shap_values_2D.shape, X_test_2D.shape

In [ ]:
x_test_2d = pd.DataFrame(data = X_test_2D, columns = nin_names)

In [ ]:
x_test_2d.corr()

In [ ]:
shap_values_2D.shape

In [ ]:
x_test_2d.shape

In [ ]:
shap.summary_plot(shap_values_2D, x_test_2d)

In [ ]:
shap.summary_plot(shap_values_2D, x_test_2d, plot_type="bar")

In [ ]:
len_test_set = X_test_2D.shape[0]
len_test_set

In [ ]:
## SHAP for each time step
NUM_STEPS = 50
NUM_FEATURES = 4


# step = 0
for step in range(NUM_STEPS):
    indice = [i for i in list(range(len_test_set)) if i%NUM_STEPS == step]
    shap_values_2D_step = shap_values_2D[indice]
    x_test_2d_step = x_test_2d.iloc[indice]
    print("_______ time step {} ___________".format(step))
    shap.summary_plot(shap_values_2D_step, x_test_2d_step, plot_type="bar")
    shap.summary_plot(shap_values_2D_step, x_test_2d_step)
    print("\n")

In [ ]:
# Create a list of tuples so that the index of the label is what is returned
tuple_of_labels = list(zip(nin_names, range(len(nin_names))))

# Create a widget for the labels and then display the widget
current_label = widgets.Dropdown(options = tuple_of_labels,
                                 value = 0,
                                 description = 'Select Label:')

# Display the dropdown list (Note: access index value with 'current_label.value')
current_label

In [ ]:
np.array(shap_values1_explainer2).shape

In [ ]:
X_test[:1,:,:].shape

In [ ]:
shap_values1_explainer2[0][0][0][:]

In [ ]:
print(f'Current label Shown: {nin_names[current_label.value]}')

shap.force_plot(base_value = explainer2.expected_value[0],
                shap_values = shap_values1_explainer2[0][0][0][current_label.value],
                features = X_test[:1,:,:][0][current_label.value],
                feature_names = nin_names)

In [ ]:
print(f'Current Label Shown: {nin_names[current_label.value]}\n')

shap.summary_plot(shap_values = shap_values1_explainer2[current_label.value][0],
                  features = X_test[:1,:,:][0],
                  feature_names = nin_names,
                  plot_type='dot')

### dependence_plots

In [ ]:
shap.dependence_plot(
            ind=0,
            shap_values=shap_values1_explainer3[0][0],
            features=X_test[:1,:,:][0],
            feature_names=nin_names,
            interaction_index=1)

In [ ]:
# code for X_test[:1,:,:]
shap.dependence_plot(
            ind=0,
            shap_values=shap_values1_explainer3_reshaped[0],
            features=X_test[:1,:,:][0],
            feature_names=nin_names,
            interaction_index=1)

In [ ]:
shap.dependence_plot(
            ind=1,
            shap_values=shap_values1_explainer3[0][0],
            features=X_test[:1,:,:][0],
            feature_names=nin_names,
            interaction_index=3)

In [ ]:
# code for X_test[:1,:,:]
shap.dependence_plot(
            ind=1,
            shap_values=shap_values1_explainer3_reshaped[0],
            features=X_test[:1,:,:][0],
            feature_names=nin_names,
            interaction_index=3)

In [ ]:
for i in range(200):
    for j in range(len(nin_names)):
        shap.dependence_plot(
                ind=j,
                shap_values=shap_values1_explainer3[i][0],
                features=X_test[0],
                feature_names=nin_names)

In [ ]:
# code for X_test[:1,:,:]
for i in range(200):
    for j in range(len(nin_names)):
        print(i)
        print(j)
        shap.dependence_plot(
                ind=j,
                shap_values=shap_values1_explainer3_reshaped[i],
                features=X_test[0],
                feature_names=nin_names)

### bar_plots
It shows a bar plot of shap values' impact on the prediction of a particular sample.

In [ ]:
for i in range(len(shap_values1_explainer3)):
    print(i)
    shap.bar_plot(shap_values=shap_values1_explainer3[i][0][0], features=X_test[:1,:,:][0][0], feature_names=nin_names)   

In [ ]:
# code for X_test[:1,:,:]
for i in range(len(shap_values1_explainer3)):
    print(i)
    shap.bar_plot(shap_values=shap_values1_explainer3_reshaped[i][0], features=X_test[:1,:,:][0][0], feature_names=nin_names)   

### plots.force

In [ ]:
shap.plots.force(base_value=explainer3.expected_value[0],
                 shap_values=shap_values1_explainer2[0][0],
                 features=X_test[:1,:,:][0],
                 feature_names=nin_names)

In [ ]:
# code for X_test[:1,:,:]
shap.plots.force(base_value=explainer3.expected_value[0],
                 shap_values=shap_values1_explainer3_reshaped[0],
                 features=X_test[:1,:,:][0],
                 feature_names=nin_names)

### force_plots
It plots shap values using additive force layout. It can help us see which features most positively or negatively contributed to prediction.

In [ ]:
# shap.force_plot(explainer1.expected_value[0], shap_values1_explainer1[0][0], nin_names)

In [ ]:
# shap.force_plot(explainer1.expected_value[0], shap_values2_explainer1[0][0], nin_names)

In [ ]:
shap.force_plot(explainer2.expected_value[0], shap_values1_explainer2[0][0], nin_names)

In [ ]:
# code for X_test[:1,:,:]
shap.force_plot(explainer3.expected_value[0], shap_values1_explainer3_reshaped[0], nin_names)

In [ ]:
# shap.force_plot(explainer2.expected_value[0], shap_values2_explainer2[0][0], nin_names)

In [ ]:
# shap.force_plot(explainer3.expected_value[0], shap_values1_explainer3[0][0], nin_names)

In [ ]:
# shap.force_plot(explainer3.expected_value[0], shap_values2_explainer3[0][0], nin_names)

In [ ]:
# shap.force_plot(explainer4.expected_value[0], shap_values1_explainer4[0][0], nin_names)

In [ ]:
# shap.force_plot(explainer4.expected_value[0], shap_values2_explainer4[0][0], nin_names)

In [ ]:
shap.force_plot(explainer2.expected_value[199], shap_values1_explainer2[199][0], nin_names)

In [ ]:
# code for X_test[:1,:,:]
shap.force_plot(explainer3.expected_value[199], shap_values1_explainer3_reshaped[199], nin_names)

### summary_plots
It creates a bee swarm plot of the shap values distribution of each feature of the dataset.

In [ ]:
# shap.summary_plot(shap_values1_explainer1[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
# shap.summary_plot(shap_values2_explainer1[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
shap.summary_plot(shap_values1_explainer2[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
# code for X_test[:1,:,:]
shap.summary_plot(shap_values1_explainer3_reshaped[0], plot_type='bar', feature_names=nin_names)

In [ ]:
# shap.summary_plot(shap_values2_explainer2[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
# shap.summary_plot(shap_values1_explainer3[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
# shap.summary_plot(shap_values2_explainer3[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
# shap.summary_plot(shap_values1_explainer4[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
# shap.summary_plot(shap_values2_explainer4[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
# shap.summary_plot(shap_values1_explainer5[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
# shap.summary_plot(shap_values2_explainer5[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
# shap.summary_plot(shap_values1_explainer6[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
# shap.summary_plot(shap_values2_explainer6[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
# shap.summary_plot(shap_values1_explainer7[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
# shap.summary_plot(shap_values2_explainer7[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
# shap.summary_plot(shap_values1_explainer8[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
# shap.summary_plot(shap_values2_explainer8[0][0], plot_type='bar', feature_names=nin_names)

In [ ]:
for i in range(len(shap_values1_explainer2)):
    for j in range(len(shap_values1_explainer2[0])):
        print(i)
        print(j)
#         shap.summary_plot(shap_values=shap_values1_explainer2[i][j], feature_names=nin_names, plot_type='dot')
#         shap.summary_plot(shap_values=shap_values1_explainer2[i][j], feature_names=nin_names, plot_type='bar')
        shap.summary_plot(shap_values=shap_values1_explainer2[i][j], feature_names=nin_names, plot_type='violin')

In [ ]:
# code for X_test[:1,:,:]
for i in range(len(shap_values1_explainer3)):
    print(i)
#   shap.summary_plot(shap_values=shap_values1_explainer3_reshaped[i], feature_names=nin_names, plot_type='dot')
#   shap.summary_plot(shap_values=shap_values1_explainer3_reshaped[i], feature_names=nin_names, plot_type='bar')
    shap.summary_plot(shap_values=shap_values1_explainer3_reshaped[i], feature_names=nin_names, plot_type='violin')

In [ ]:
for i in range(len(shap_values1_explainer2)):
    for j in range(len(shap_values1_explainer2[0])):
        print(i)
        print(j)
        shap.summary_plot(shap_values=shap_values1_explainer2[i][j], features=X_test[j], feature_names=nin_names, plot_type='dot')
#         shap.summary_plot(shap_values=shap_values1_explainer2[i][j], features=X_test[j], feature_names=nin_names, plot_type='bar')
#         shap.summary_plot(shap_values=shap_values1_explainer2[i][j], features=X_test[j], feature_names=nin_names, plot_type='violin')

In [ ]:
# code for X_test[:1,:,:]
for i in range(len(shap_values1_explainer3)):
    print(i)
    shap.summary_plot(shap_values=shap_values1_explainer3_reshaped[i], features=X_test[0], feature_names=nin_names, plot_type='dot')
#     shap.summary_plot(shap_values=shap_values1_explainer3_reshaped[i], features=X_test[0], feature_names=nin_names, plot_type='bar')
#     shap.summary_plot(shap_values=shap_values1_explainer3_reshaped[i], features=X_test[0], feature_names=nin_names, plot_type='violin')

### decision_plots
It shows the path of how the model reached a particular decision based on the shap values of individual features. The individual plotted line represents one sample of data and how it reached a particular prediction.

In [ ]:
# shap.decision_plot(explainer1.expected_value[0], shap_values1_explainer1[0][0], features=X_test, feature_names=nin_names)

In [ ]:
# shap.decision_plot(explainer1.expected_value[0], shap_values2_explainer1[0][0], features=X_test, feature_names=nin_names)

In [ ]:
shap.decision_plot(explainer2.expected_value[0], shap_values1_explainer2[0][0], features=X_test, feature_names=nin_names)

In [ ]:
# code for X_test[:1,:,:]
shap.decision_plot(explainer3.expected_value[0], shap_values1_explainer3_reshaped[0], features=X_test, feature_names=nin_names)

In [ ]:
# shap.decision_plot(explainer2.expected_value[0], shap_values2_explainer2[0][0], features=X_test, feature_names=nin_names)

In [ ]:
# shap.decision_plot(explainer3.expected_value[0], shap_values1_explainer3[0][0], features=X_test, feature_names=nin_names)

In [ ]:
# shap.decision_plot(explainer3.expected_value[0], shap_values2_explainer3[0][0], features=X_test, feature_names=nin_names)

In [ ]:
# shap.decision_plot(explainer4.expected_value[0], shap_values1_explainer4[0][0], features=X_test, feature_names=nin_names)

In [ ]:
# shap.decision_plot(explainer4.expected_value[0], shap_values2_explainer4[0][0], features=X_test, feature_names=nin_names)

In [ ]:
for i in range(explainer2.expected_value.shape[0]):
    print(i)
    shap.decision_plot(explainer2.expected_value[i], shap_values1_explainer2[i][0], features=X_test[:1,:,:], feature_names=nin_names)

In [ ]:
# code for X_test[:1,:,:]
for i in range(explainer3.expected_value.shape[0]):
    print(i)
    shap.decision_plot(explainer3.expected_value[i], shap_values1_explainer3_reshaped[i], features=X_test[:1,:,:], feature_names=nin_names)

In [ ]:
shap.decision_plot(explainer2.expected_value[199], shap_values1_explainer2[199][0], features=X_test[:1,:,:], feature_names=nin_names)

In [ ]:
# code for X_test[:1,:,:]
shap.decision_plot(explainer3.expected_value[199], shap_values1_explainer3_reshapedshaped[199], features=X_test[:1,:,:], feature_names=nin_names)

### multioutput_decision_plot
Its decision plot for multi-output models (multi-class classification).

In [ ]:
row_index = 0
shap.multioutput_decision_plot(explainer3.expected_value.tolist(), shap_values_reshaped.tolist(), row_index)

In [ ]:
for i in range(explainer3.expected_value.shape[0]):
    print(i)
    shap.multioutput_decision_plot(explainer3.expected_value.tolist(), shap_values_reshaped.tolist(), row_index=i, feature_names=nin_names_names)    

### plots._waterfall.waterfall_legacy
It shows a waterfall plot explaining a particular prediction of the model based on shap values. It kind of shows the path of how shap values were added to the base value to come to a particular prediction.

In [ ]:
# shap.plots._waterfall.waterfall_legacy(explainer1.expected_value[0], shap_values1_explainer1[0][0][0], feature_names=nin_names)

In [ ]:
# shap.plots._waterfall.waterfall_legacy(explainer1.expected_value[0], shap_values2_explainer1[0][0][0], feature_names=nin_names)

In [ ]:
shap.plots._waterfall.waterfall_legacy(explainer3.expected_value[0], shap_values1_explainer3[0][0][0], feature_names=nin_names)

In [ ]:
# code for X_test[:1,:,:]
shap.plots._waterfall.waterfall_legacy(explainer3.expected_value[0], shap_values1_explainer3_reshaped[0][0], feature_names=nin_names)

In [ ]:
# shap.plots._waterfall.waterfall_legacy(explainer2.expected_value[0], shap_values2_explainer2[0][0][0], feature_names=nin_names)

In [ ]:
# shap.plots._waterfall.waterfall_legacy(explainer3.expected_value[0], shap_values1_explainer3[0][0][0], feature_names=nin_names)

In [ ]:
# shap.plots._waterfall.waterfall_legacy(explainer3.expected_value[0], shap_values2_explainer3[0][0][0], feature_names=nin_names)

In [ ]:
# shap.plots._waterfall.waterfall_legacy(explainer4.expected_value[0], shap_values1_explainer4[0][0][0], feature_names=nin_names)

In [ ]:
# shap.plots._waterfall.waterfall_legacy(explainer4.expected_value[0], shap_values2_explainer4[0][0][0], feature_names=nin_names)

In [ ]:
shap.plots._waterfall.waterfall_legacy(explainer2.expected_value[199], shap_values1_explainer2[199][0][49], feature_names=nin_names)

In [ ]:
# code for X_test[:1,:,:]
shap.plots._waterfall.waterfall_legacy(explainer3.expected_value[199], shap_values1_explainer3_reshaped[199][49], feature_names=nin_names)

In [ ]:
for i in range(explainer2.expected_value.shape[0]):
    print(i)
    shap.plots._waterfall.waterfall_legacy(explainer2.expected_value[i],
                                           shap_values1_explainer2[i][0][0],
                                           feature_names=nin_names)        

In [ ]:
# code for X_test[:1,:,:]
for i in range(explainer3.expected_value.shape[0]):
    print(i)
    shap.plots._waterfall.waterfall_legacy(explainer3.expected_value[i],
                                           shap_values1_explainer3_reshaped[i][0],
                                           feature_names=nin_names)        

#### Ensure the sum of Shapley values matches the difference between predicted value and expected value: For each instance in your dataset, the sum of the Shapley values across all features should add up to the difference between the model's predicted value for that instance and the expected value.

In [24]:
np.array(shap_values1_explainer3).shape

(200, 1, 50, 4)

In [25]:
explainer3.expected_value.shape

(200,)

In [26]:
np.array(shap_values1_explainer4).shape

(200, 1, 50, 4)

In [27]:
explainer4.expected_value.shape

(200,)

In [30]:
predicted_values_1 = model.predict(X_test[:1,:,:])
predicted_values_1.shape

(1, 200)

In [29]:
predicted_values_10 = model.predict(X_test)
predicted_values_10.shape

(10, 200)

In [32]:
for i in range(len(X_test[:1,:,:])):
    for j in range(predicted_values_1.shape[1]):
        shap_sum = np.sum(shap_values1_explainer3[j][i])
        pred_diff = predicted_values[i, j] - explainer3.expected_value[j]
        print(f"Instance {i+1}, Output {j+1}: Shapley sum = \t{shap_sum}, \n\tPredicted difference = \t\t{pred_diff}")

Instance 1, Output 1: Shapley sum = 	0.03931541483116244, 
	Predicted difference = 		0.03931540995836258
Instance 1, Output 2: Shapley sum = 	0.0624836190854907, 
	Predicted difference = 		0.06248363479971886
Instance 1, Output 3: Shapley sum = 	0.07892198175359516, 
	Predicted difference = 		0.07892195880413055
Instance 1, Output 4: Shapley sum = 	0.008039699394946916, 
	Predicted difference = 		0.008039727807044983
Instance 1, Output 5: Shapley sum = 	0.05387160711774695, 
	Predicted difference = 		0.05387163907289505
Instance 1, Output 6: Shapley sum = 	0.08079164116772264, 
	Predicted difference = 		0.0807916522026062
Instance 1, Output 7: Shapley sum = 	0.11009368714430227, 
	Predicted difference = 		0.11009369790554047
Instance 1, Output 8: Shapley sum = 	0.021762403191580904, 
	Predicted difference = 		0.021762404590845108
Instance 1, Output 9: Shapley sum = 	0.0643267919990298, 
	Predicted difference = 		0.06432679295539856
Instance 1, Output 10: Shapley sum = 	0.08833670441779

In [34]:
for i in range(len(X_test)):
    for j in range(predicted_values_10.shape[1]):
        shap_sum = np.sum(shap_values1_explainer3[j][i])
        pred_diff = predicted_values[i, j] - explainer3.expected_value[j]
        print(f"Instance {i+1}, Output {j+1}: Shapley sum = \t{shap_sum}, \n\tPredicted difference = \t\t{pred_diff}")

Instance 1, Output 1: Shapley sum = 	0.03931541483116244, 
	Predicted difference = 		0.03931540995836258
Instance 1, Output 2: Shapley sum = 	0.0624836190854907, 
	Predicted difference = 		0.06248363479971886
Instance 1, Output 3: Shapley sum = 	0.07892198175359516, 
	Predicted difference = 		0.07892195880413055
Instance 1, Output 4: Shapley sum = 	0.008039699394946916, 
	Predicted difference = 		0.008039727807044983
Instance 1, Output 5: Shapley sum = 	0.05387160711774695, 
	Predicted difference = 		0.05387163907289505
Instance 1, Output 6: Shapley sum = 	0.08079164116772264, 
	Predicted difference = 		0.0807916522026062
Instance 1, Output 7: Shapley sum = 	0.11009368714430227, 
	Predicted difference = 		0.11009369790554047
Instance 1, Output 8: Shapley sum = 	0.021762403191580904, 
	Predicted difference = 		0.021762404590845108
Instance 1, Output 9: Shapley sum = 	0.0643267919990298, 
	Predicted difference = 		0.06432679295539856
Instance 1, Output 10: Shapley sum = 	0.08833670441779

IndexError: index 1 is out of bounds for axis 0 with size 1

In [35]:
for i in range(len(X_test[:1,:,:])):
    for j in range(predicted_values_1.shape[1]):
        shap_sum = np.sum(shap_values1_explainer4[j][i])
        pred_diff = predicted_values[i, j] - explainer4.expected_value[j]
        print(f"Instance {i+1}, Output {j+1}: Shapley sum = \t{shap_sum}, \n\tPredicted difference = \t\t{pred_diff}")

Instance 1, Output 1: Shapley sum = 	0.041457514837384225, 
	Predicted difference = 		0.041457485407590866
Instance 1, Output 2: Shapley sum = 	0.07950845528393984, 
	Predicted difference = 		0.07950848340988159
Instance 1, Output 3: Shapley sum = 	0.09368795640766621, 
	Predicted difference = 		0.09368789941072464
Instance 1, Output 4: Shapley sum = 	0.02726304717361927, 
	Predicted difference = 		0.027263104915618896
Instance 1, Output 5: Shapley sum = 	0.05932366829365491, 
	Predicted difference = 		0.05932368338108063
Instance 1, Output 6: Shapley sum = 	0.10405436502769588, 
	Predicted difference = 		0.10405440628528595
Instance 1, Output 7: Shapley sum = 	0.13229086967185139, 
	Predicted difference = 		0.1322908103466034
Instance 1, Output 8: Shapley sum = 	0.04884388875216246, 
	Predicted difference = 		0.04884396120905876
Instance 1, Output 9: Shapley sum = 	0.07471523899585009, 
	Predicted difference = 		0.07471524178981781
Instance 1, Output 10: Shapley sum = 	0.1153550722636

In [36]:
for i in range(len(X_test)):
    for j in range(predicted_values_10.shape[1]):
        shap_sum = np.sum(shap_values1_explainer4[j][i])
        pred_diff = predicted_values[i, j] - explainer4.expected_value[j]
        print(f"Instance {i+1}, Output {j+1}: Shapley sum = \t{shap_sum}, \n\tPredicted difference = \t\t{pred_diff}")

Instance 1, Output 1: Shapley sum = 	0.041457514837384225, 
	Predicted difference = 		0.041457485407590866
Instance 1, Output 2: Shapley sum = 	0.07950845528393984, 
	Predicted difference = 		0.07950848340988159
Instance 1, Output 3: Shapley sum = 	0.09368795640766621, 
	Predicted difference = 		0.09368789941072464
Instance 1, Output 4: Shapley sum = 	0.02726304717361927, 
	Predicted difference = 		0.027263104915618896
Instance 1, Output 5: Shapley sum = 	0.05932366829365491, 
	Predicted difference = 		0.05932368338108063
Instance 1, Output 6: Shapley sum = 	0.10405436502769588, 
	Predicted difference = 		0.10405440628528595
Instance 1, Output 7: Shapley sum = 	0.13229086967185139, 
	Predicted difference = 		0.1322908103466034
Instance 1, Output 8: Shapley sum = 	0.04884388875216246, 
	Predicted difference = 		0.04884396120905876
Instance 1, Output 9: Shapley sum = 	0.07471523899585009, 
	Predicted difference = 		0.07471524178981781
Instance 1, Output 10: Shapley sum = 	0.1153550722636

IndexError: index 1 is out of bounds for axis 0 with size 1

In [37]:
def verify_shap_values(shap_values, expected_values, predicted_values):
    """
    Verify the correctness of SHAP values.

    Args:
        shap_values (numpy.ndarray): Array of SHAP values with shape (n_instances, 1, n_features, n_classes).
        expected_values (numpy.ndarray): Array of expected values with shape (n_instances,).
        predicted_values (numpy.ndarray): Array of predicted values with shape (1, n_instances).

    Returns:
        bool: True if the SHAP values are correctly calculated, False otherwise.
    """
    
    # Step 1: Verify shapes
    n_instances, _, n_features, n_classes = shap_values.shape
    _, n_instances_predicted = predicted_values.shape

    if n_instances != n_instances_predicted:
        print("Error: Number of instances in shap_values and predicted_values do not match.")
        return False

    # Step 2: Check the sum property
    for i in range(n_instances):
        sum_shap_values = np.sum(shap_values[i, 0, :, :])
        diff_predicted_expected = predicted_values[0, i] - expected_values[i]
        
        print(sum_shap_values)
        print(diff_predicted_expected)

        if not np.isclose(sum_shap_values, diff_predicted_expected):
            print(f"Error: Sum of SHAP values for instance {i} does not match the difference between predicted and expected values.")
            return False

    return True

In [38]:
verify_shap_values(np.array(shap_values1_explainer3), explainer3.expected_value, predicted_values_1)

0.03931541483116244
0.03931541
0.0624836190854907
0.062483635
0.07892198175359516
0.07892196
0.008039699394946916
0.008039728
0.05387160711774695
0.05387164
0.08079164116772264
0.08079165
0.11009368714430227
0.1100937
0.021762403191580904
0.021762405
0.0643267919990298
0.06432679
0.08833670441779308
0.088336706
0.12609328911961618
0.12609331
0.0327630699531227
0.03276308
0.07484774650652218
0.074847765
0.09245039417449011
0.092450395
0.13560600727310568
0.13560598
0.040818951770548
0.040819004
0.08537595688523257
0.085375965
0.09503754998243413
0.09503754
0.14128786606188945
0.14128788
0.04711052670459984
0.047110554
0.09522063971764314
0.09522064
0.0967823131972194
0.0967823
0.14432033561901608
0.14432034
0.05246324907545094
0.052463207
0.10388368055868893
0.10388371
0.0980269993037003
0.098027006
0.1454776181639532
0.14547761
0.05725116510490001
0.05725119
0.11114604188478808
0.111145996
0.09896875183006701
0.098968744
0.14535440699603264
0.14535442
0.061589507715690175
0.061589547
0

True

In [39]:
verify_shap_values(np.array(shap_values2_explainer3), explainer3.expected_value, predicted_values_10)

0.03931541483116244
0.03931541
0.0624836190854907
0.062483627
0.07892198175359516
0.07892197
0.008039699394946916
0.008039713
0.05387160711774695
0.05387164
0.08079164116772264
0.08079165
0.11009368714430227
0.1100937
0.021762403191580904
0.021762405
0.0643267919990298
0.06432679
0.08833670441779308
0.088336706
0.12609328911961618
0.12609331
0.0327630699531227
0.03276308
0.07484774650652218
0.074847795
0.09245039417449011
0.092450365
0.13560600727310568
0.135606
0.040818951770548
0.040818945
0.08537595688523257
0.085375965
0.09503754998243413
0.09503756
0.14128786606188945
0.1412879
0.04711052670459984
0.047110554
0.09522063971764314
0.09522064
0.0967823131972194
0.0967823
0.14432033561901608
0.14432034
0.05246324907545094
0.052463207
0.10388368055868893
0.10388371
0.0980269993037003
0.098026976
0.1454776181639532
0.14547764
0.05725116510490001
0.05725119
0.11114604188478808
0.111146055
0.09896875183006701
0.098968744
0.14535440699603264
0.14535445
0.061589507715690175
0.061589487
0.11

True

In [40]:
verify_shap_values(np.array(shap_values1_explainer4), explainer4.expected_value, predicted_values_1)

0.041457514837384225
0.041457485
0.07950845528393984
0.07950848
0.09368795640766621
0.0936879
0.02726304717361927
0.027263105
0.05932366829365491
0.059323683
0.10405436502769588
0.10405441
0.13229086967185139
0.13229081
0.04884388875216246
0.04884396
0.07471523899585009
0.07471524
0.11535507226362823
0.11535509
0.15385038889944552
0.15385039
0.0633621851913631
0.06336224
0.09080312540754676
0.09080314
0.12249622126109896
0.12249623
0.16788783639203755
0.16788778
0.07348720431327818
0.073487304
0.10676317196339369
0.106763214
0.12770935972221195
0.12770936
0.1771363018429838
0.17713629
0.08148458078503606
0.08148462
0.1215135877020657
0.1215136
0.13175415800651535
0.13175415
0.18287184104556217
0.18287183
0.08850556584075092
0.08850557
0.1344133666716516
0.1344134
0.13500956068746744
0.13500956
0.18602241631015204
0.18602237
0.09496572552016005
0.09496576
0.14523540567606685
0.14523534
0.13770184349268674
0.13770182
0.18734732912271282
0.1873473
0.10093547850847244
0.10093556
0.15402291

True

In [41]:
verify_shap_values(np.array(shap_values2_explainer4), explainer4.expected_value, predicted_values_10)

0.041457514837384225
0.041457485
0.07950845528393984
0.079508476
0.09368795640766621
0.093687914
0.02726304717361927
0.02726309
0.05932366829365491
0.059323683
0.10405436502769588
0.10405441
0.13229086967185139
0.13229081
0.04884388875216246
0.04884396
0.07471523899585009
0.07471524
0.11535507226362823
0.11535509
0.15385038889944552
0.15385039
0.0633621851913631
0.06336224
0.09080312540754676
0.09080317
0.12249622126109896
0.1224962
0.16788783639203755
0.1678878
0.07348720431327818
0.073487245
0.10676317196339369
0.106763214
0.12770935972221195
0.12770937
0.1771363018429838
0.1771363
0.08148458078503606
0.08148462
0.1215135877020657
0.1215136
0.13175415800651535
0.13175415
0.18287184104556217
0.18287183
0.08850556584075092
0.08850557
0.1344133666716516
0.1344134
0.13500956068746744
0.13500953
0.18602241631015204
0.1860224
0.09496572552016005
0.09496576
0.14523540567606685
0.1452354
0.13770184349268674
0.13770182
0.18734732912271282
0.18734732
0.10093547850847244
0.100935504
0.154022915

True